In [5]:
import requests
from urllib.error import HTTPError
import io
from urllib.request import urlopen
import pandas as pd
import numpy as np
import awswrangler as wr
from tqdm.notebook import tqdm


In [19]:
import requests
from bs4 import BeautifulSoup

# URL of the Standard Meteorological Dataset page
url = "https://www.ndbc.noaa.gov/historical_data.shtml"

# Make a GET request to the URL
response = requests.get(url)

# Create a BeautifulSoup object to parse the HTML content
soup = BeautifulSoup(response.text, 'html.parser')

# # Find all the links to station data
# station_links = soup.find_all('a', href=lambda href: href.startswith('/view_data.php?station='))

# # Extract the station ID from each link
# station_ids = [link['href'].split('=')[1] for link in station_links]

# # Print the station IDs and links
# for station_id, link in zip(station_ids, station_links):
#     print(f"Station ID: {station_id}, Link: {link}")

In [20]:
soup

<!DOCTYPE html>

<html lang="en">
<head>
<title>NDBC - Historical NDBC Data</title>
<meta content="width=device-width, initial-scale=1.0" name="viewport"/>
<meta content="text/html; charset=utf-8" http-equiv="content-type"/>
<meta content="What's New at the NDBC Web Site?" name="DC.title"/>
<meta content="The National Data Buoy Center's page for new events." name="DC.description"/>
<meta content="weather, buoy, weather buoy, marine, forecast, hurricane, wind, wave, offshore, surfing, temperature, meteorology, climate, ocean" name="DC.subject"/>
<meta content="US Department of Commerce, National Oceanic and Atmospheric Administration, National Weather Service, National Data Buoy Center" name="DC.creator"/>
<meta content="EN-US" name="DC.language" scheme="DCTERMS.RFC1766"/>
<meta content="text/html;charset=iso-8859-1" name="DC.format"/>
<meta content="1996-11-08" name="DC.date.created" scheme="ISO8601"/>
<meta content="2024-02-06" name="DC.date.reviewed" scheme="ISO8601"/>
<meta content=

In [21]:
# Find the element containing the text "Standard Meteorological"
element = soup.find('b', string="Standard Meterological")  

bouy_data_links = dict()

# Get the parent of the element
parent = element.parent 
liem = parent.find('ul')

# Print the parent element (or its contents)
for x in liem.find_all('li'):
    
    # print(x.text.split(':')[0])
    # print(x.find_all('a'))
    # for y in x.children:
    #     print(y.href)
    #     print(y.text)
    bouy_id = x.text.split(':')[0]
    links = list()
    for y in x.find_all('a'):
        link = 'https://www.ndbc.noaa.gov/view_text_file.php?' + y['href'].split('?')[-1]
        year = y.text
        links.append((year, link))
    bouy_data_links[bouy_id] = links
        # https://www.ndbc.noaa.gov/view_text_file.php?filename=18ci3h2015.txt.gz&dir=data/historical/stdmet/

In [3]:
len(bouy_data_links)

1315

In [4]:
bouy_data_links.keys()

dict_keys(['0Y2W3', '18CI3', '20CM4', '23020', '31201', '32012', '32301', '32302', '32487', '32488', '32ST1', '32ST2', '34002', '41001', '41002', '41003', '41004', '41005', '41006', '41007', '41008', '41009', '41010', '41011', '41012', '41013', '41015', '41016', '41017', '41018', '41021', '41022', '41023', '41024', '41025', '41027', '41029', '41030', '41033', '41035', '41036', '41037', '41038', '41040', '41041', '41043', '41044', '41046', '41047', '41048', '41049', '41051', '41052', '41053', '41056', '41057', '41058', '41060', '41061', '41062', '41063', '41064', '41065', '41066', '41067', '41068', '41069', '41070', '41076', '41108', '41109', '41110', '41112', '41113', '41114', '41115', '41116', '41117', '41118', '41119', '41120', '41121', '41122', '41140', '41141', '41159', '41193', '41194', '41NT1', '41NT2', '42001', '42002', '42003', '42004', '42005', '42006', '42007', '42008', '42009', '42010', '42011', '42012', '42013', '42014', '42015', '42016', '42017', '42018', '42019', '42020',

In [5]:
import pandas as pd

In [40]:
pd.read_xml('https://www.ndbc.noaa.gov/metadata/stationmetadata.xml')

id                                               name  \
0       0Y2W3                        Sturgeon Bay CG Station, WI   
1     1801583  SD 1063 - 24 NM SSW of San Francisco, CA (Site...   
2       18CI3                       Michigan City CG Station, IN   
3       20CM4                          St. Joseph CG Station, MI   
4       21346                  21346  380km East of Iwate, Japan   
...       ...                                                ...   
1469    YGNN6                    Niagara Coast Guard Station, NY   
1470    YKRV2     8637611 - York River East Rear Range Light, VA   
1471    YKTV2        8637689 - Yorktown USCG Training Center, VA   
1472    YRSV2         Taskinas Creek, Chesapeake Bay Reserve, VA   
1473    ZBQN7                       Zeke's Basin, North Carolina   

                                           owner                        pgm  \
0             U.S.C.G. Marine Reporting Stations              IOOS Partners   
1                                           NDBC  NDBC Meteorological/Ocean   
2             U.S.C.G. Marine Reporting Stations              IOOS Partners   
3             U.S.C.G. Marine Reporting Stations              IOOS Partners   
4                 Japanese Meteorological Agency                    Tsunami   
...                                          ...                        ...   
1469                          NWS Eastern Region              IOOS Partners   
1470                              NOAA NOS PORTS                 NOS/CO-OPS   
1471                                         NOS                 NOS/CO-OPS   
1472  National Estuarine Research Reserve System                      NERRS   
1473  National Estuarine Research Reserve System                      NERRS   

       type  history  
0     fixed      NaN  
1     other      NaN  
2     fixed      NaN  
3     fixed      NaN  
4      dart      NaN  
...     ...      ...  
1469  fixed      NaN  
1470  fixed      NaN  
1471  fixed      NaN  
1472  fixed      NaN  
1473  fixed      NaN  

[1474 rows x 6 columns]

In [6]:
import requests

# URL of the JSON data
url = "https://www.ndbc.noaa.gov/ndbcmapstations.json"

# Make a GET request to the URL
response = requests.get(url)

# Get the JSON data from the response
data = response.json()

# Print the JSON data
print(data.keys())

dict_keys(['disclaimer', 'created', 'count', 'program', 'owner', 'station', 'dartevents'])


In [8]:
sd  = pd.DataFrame(data['station'])

In [9]:
sd

id     lat     lon   elev  \
0     0y2w3  44.794 -87.313  179.0   
1     13001  12.000 -23.000    0.0   
2     13002  21.000 -23.000    0.0   
3     13008  15.000 -38.000    0.0   
4     13009   8.000 -38.000    0.0   
...     ...     ...     ...    ...   
1899  ygnn6  43.262 -79.064   73.0   
1900  ykrv2  37.251 -76.342    NaN   
1901  yktv2  37.227 -76.479    3.7   
1902  yrsv2  37.414 -76.712   11.0   
1903  zbqn7  33.955 -77.935    NaN   

                                                name  owner  program status  \
0                        Sturgeon Bay CG Station, WI    106        2      E   
1                                       NE Extension     84        1      E   
2                                       NE Extension     84        1      E   
3                                             Reggae     84        1      E   
4                                            Lambada     84        1      E   
...                                              ...    ...      ...    ...   
1899                 Niagara Coast Guard Station, NY     82        2      E   
1900  8637611 - York River East Rear Range Light, VA     73        5      D   
1901     8637689 - Yorktown USCG Training Center, VA     78        5      E   
1902      Taskinas Creek, Chesapeake Bay Reserve, VA     64        4      E   
1903                    Zeke's Basin, North Carolina     64        4      E   

     data   type  seq  
0       n  fixed  NaN  
1       y   buoy  NaN  
2       y   buoy  NaN  
3       y   buoy  NaN  
4       n   buoy  NaN  
...   ...    ...  ...  
1899    y  fixed  NaN  
1900    n  fixed  NaN  
1901    y  fixed  NaN  
1902    y  fixed  NaN  
1903    n  fixed  NaN  

[1904 rows x 11 columns]

In [10]:
sd['owner'] = sd.apply(lambda x: data['owner'][x.owner], axis=1)

In [11]:
sd['program'] = sd.apply(lambda x: data['program'][x.program], axis=1)

In [12]:
sd.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1904 entries, 0 to 1903
Data columns (total 11 columns):
 #   Column   Non-Null Count  Dtype  
---  ------   --------------  -----  
 0   id       1904 non-null   object 
 1   lat      1904 non-null   float64
 2   lon      1904 non-null   float64
 3   elev     1350 non-null   float64
 4   name     1904 non-null   object 
 5   owner    1904 non-null   object 
 6   program  1904 non-null   object 
 7   status   1904 non-null   object 
 8   data     1904 non-null   object 
 9   type     1904 non-null   object 
 10  seq      55 non-null     object 
dtypes: float64(3), object(8)
memory usage: 163.8+ KB


In [57]:
import awswrangler as wr

In [58]:
wr.s3.to_parquet(sd, 's3://gulf-waves/data/raw/station_metadata/file.parquet')

{'paths': ['s3://gulf-waves/data/raw/station_metadata/file.parquet'],
 'partitions_values': {}}

In [212]:
[1,2,3][:2]

[1, 2]

In [13]:
bouy_data_links.items()

dict_items([('0Y2W3', [('2012', 'https://www.ndbc.noaa.gov/view_text_file.php?filename=0y2w3h2012.txt.gz&dir=data/historical/stdmet/'), ('2013', 'https://www.ndbc.noaa.gov/view_text_file.php?filename=0y2w3h2013.txt.gz&dir=data/historical/stdmet/'), ('2014', 'https://www.ndbc.noaa.gov/view_text_file.php?filename=0y2w3h2014.txt.gz&dir=data/historical/stdmet/'), ('2015', 'https://www.ndbc.noaa.gov/view_text_file.php?filename=0y2w3h2015.txt.gz&dir=data/historical/stdmet/')]), ('18CI3', [('2014', 'https://www.ndbc.noaa.gov/view_text_file.php?filename=18ci3h2014.txt.gz&dir=data/historical/stdmet/'), ('2015', 'https://www.ndbc.noaa.gov/view_text_file.php?filename=18ci3h2015.txt.gz&dir=data/historical/stdmet/')]), ('20CM4', [('2014', 'https://www.ndbc.noaa.gov/view_text_file.php?filename=20cm4h2014.txt.gz&dir=data/historical/stdmet/'), ('2015', 'https://www.ndbc.noaa.gov/view_text_file.php?filename=20cm4h2015.txt.gz&dir=data/historical/stdmet/')]), ('23020', [('2008', 'https://www.ndbc.noaa.go

In [116]:
from urllib.error import HTTPError
import io
from urllib.request import urlopen
import pandas as pd
import numpy as np
import awswrangler as wr

columns = [
    'year',
    'month',
    'day',
    'hour',
    'minute',
    'wind_dir',
    'wind_spd',
    'gust',
    'wave_height',
    'dominant_period',
    'avg_period',
    'wave_direction',
    'pressure',
    'air_temp',
    'water_temp',
    'dew_point',
    'visibility',
    'tide'
]

columns_no_minutes = [
    'year',
    'month',
    'day',
    'hour',
    'wind_dir',
    'wind_spd',
    'gust',
    'wave_height',
    'dominant_period',
    'avg_period',
    'wave_direction',
    'pressure',
    'air_temp',
    'water_temp',
    'dew_point',
    'visibility',
    'tide'
]

col_nans = {
    'wind_dir': 999,
    'wind_spd': 99.0,
    'gust': 99.0,
    'wave_height': 99.0,
    'dominant_period': 99.0,
    'avg_period': 99.0,
    'wave_direction': 999,
    'pressure': 9999.0,
    'air_temp': 999.0,
    'water_temp': 999.0,
    'dew_point': 99.0,
    'visibility': 99.0,
    'tide': 99.0
}

def nan_cols(col: pd.Series):
    if col.name not in col_nans:
        return col
    return col.replace(col_nans[col.name], np.nan)
    
def load_em_datums(station_id, uris, save_frame=True):
    hist_waves = list()
            # file_uri = f'https://www.ndbc.noaa.gov/view_text_file.php?filename={station_id}h{year}.txt.gz&dir=data/historical/stdmet/'
    for year, uri in uris:        
    
        with urlopen(uri) as response:
            # file = response.read()
            file_bytes = io.BytesIO(response.read())


        file_line_one = file_bytes.readline()
        # print(file_line_one[:4])
        # has_minutes = not file_line_one[:3] in ['YY ', 'YYY']
        has_minutes = 'mm' in str(file_line_one)
        skip_two = '#' in str(file_line_one)
        # skip_two = str(file_line_one)[0] == '#'
        # print(year)
        print(year, '-',file_line_one)
        # print(has_minutes)
        # print(skip_two)
        # print(str(file_line_one)[0])
        df_args = {
           'skiprows': 2 if skip_two else 1,
            'names': columns if has_minutes else columns_no_minutes,
            'infer_nrows': 50
        }
        # print(file_bytes.readline())
        file_bytes.seek(0)
        # print(df_args)
        df = pd.read_fwf(file_bytes, **df_args)
        if not has_minutes:
            df.loc[:, ('minute',)] = np.nan
            df = df[columns]
        df['source'] = uri
        hist_waves.append(df)
        # print(f'Found {year} at {file_uri}')
    out_df = pd.concat(hist_waves).apply(nan_cols)
    if save_frame:
        s3_location = f's3://gulf-waves/data/raw/historic_smd/station_id={station_id}/file.parquet'
        wr.s3.to_parquet(out_df, s3_location)
    else:
        return out_df, hist_waves

In [ ]:
YY MM DD hh WD   WSPD GST  WVHT  DPD   APD  MWD  BAR    ATMP  WTMP  DEWP  VIS
81 02 19 00 999 99.0 99.0 03.70 12.50 06.90 999 9999.0 999.0 999.0 999.0 99.0

In [38]:
import requests
from io import StringIO

colspecs_98 =  {
                'year': ((0,2), int),
                'month': ((3,5), int),
                'day': ((6,8), int),
                'hour': ((9,11), int),
                'wind_dir': ((12,15), pd.Int64Dtype()),
                'wind_spd': ((16,20), float),
                'gust': ((21,25), float),
                'wave_height': ((26,31), float),
                'dominant_period': ((32,37), float),
                'avg_period': ((38,43), float),
                'wave_direction': ((44,47), pd.Int64Dtype()),
                'pressure': ((48,54), float),
                'air_temp': ((55,60), float),
                'water_temp': ((61,66), float),
                'dew_point': ((67,72), float),
                'visibility': ((73,77), float),
        }

colspecs_99 = {
                'year': ((0,4), int),
                'month': ((5,7), int),
                'day': ((8,10), int),
                'hour': ((11,13), int),
                'wind_dir': ((14,17), pd.Int64Dtype()),
                'wind_spd': ((18,22), float),
                'gust': ((23,27), float),
                'wave_height': ((28,33), float),
                'dominant_period': ((34,39), float),
                'avg_period': ((40,45), float),
                'wave_direction': ((46,49), pd.Int64Dtype()),
                'pressure': ((50,56), float),
                'air_temp': ((57,62), float),
                'water_temp': ((63,68), float),
                'dew_point': ((69,74), float),
                'visibility': ((75,79), float),
        }

colspecs_04 = {
                'year': ((0,4), int),
                'month': ((5,7), int),
                'day': ((8,10), int),
                'hour': ((11,13), int),
                'wind_dir': ((14,17), pd.Int64Dtype()),
                'wind_spd': ((18,22), float),
                'gust': ((23,27), float),
                'wave_height': ((28,33), float),
                'dominant_period': ((34,39), float),
                'avg_period': ((40,45), float),
                'wave_direction': ((46,49), pd.Int64Dtype()),
                'pressure': ((50,56), float),
                'air_temp': ((57,62), float),
                'water_temp': ((63,68), float),
                'dew_point': ((69,74), float),
                'visibility': ((75,79), float),
                'tide': ((80,85), float)
        }

colspecs_23 = {
                'year': ((0,4), int),
                'month': ((5,7), int),
                'day': ((8,10), int),
                'hour': ((11,13), int),
                'minute': ((14,16), int),
                'wind_dir': ((17,20), pd.Int64Dtype()),
                'wind_spd': ((21,25), float),
                'gust': ((26,30), float),
                'wave_height': ((31,36), float),
                'dominant_period': ((37,42), float),
                'avg_period': ((43,48), float),
                'wave_direction': ((49,52), pd.Int64Dtype()),
                'pressure': ((53,59), float),
                'air_temp': ((60,65), float),
                'water_temp': ((66,71), float),
                'dew_point': ((72,77), float),
                'visibility': ((78,82), float),
                'tide': ((83,88), float)
        }


col_nans = {
    'wind_dir': 999,
    'wind_spd': 99.0,
    'gust': 99.0,
    'wave_height': 99.0,
    'dominant_period': 99.0,
    'avg_period': 99.0,
    'wave_direction': 999,
    'pressure': 9999.0,
    'air_temp': 999.0,
    'water_temp': 999.0,
    'dew_point': 99.0,
    'visibility': 99.0,
    'tide': 99.0
}   


def replace_comma_with_dot_float(value):
    return float(value.replace(',', '.'))


def nan_cols(col: pd.Series):
    if col.name not in col_nans:
        return col
    return col.replace(col_nans[col.name], np.nan)
   

def process_line(line, length, current_line, itermax=10):
    o_line = line.replace(',', '.')
    negs = line.count('-')
    iters = 0
    # print(line)
    if current_line > 3 and o_line.startswith('#'):
        return ''

    o_line = o_line.replace('-5143.9','99.0')
    o_line = o_line.replace('-5572.8','999.0')
    o_line = o_line.replace(' MM', '999')

    while iters < itermax and len(o_line) != length:
        o_line = o_line.replace(' -999.00 ', ' 99.00 ')
        if len(line) == length + 1:
            o_line = o_line.replace(' -9999.0 ', '9999.0')
            o_line = o_line.replace(' -999.0 ',' 999.0 ')
        if len(line) == length + 2:
            o_line = o_line.replace('-9999.0', '999.0')
        if len(line) == length + 3:
            o_line = o_line.replace('-9999.0', '99.0')
        iters += 1
    if len(o_line) != length:
        return ''
    return o_line
    

def load_em_datums(station_id, uris, save_frame=True, log_uri=False):
    hist_waves = list()
    for year, uri in uris:
        # print(year, '-',uri)
        if int(year) < 1999:
            spec = colspecs_98
            skiprows = 1
        elif int(year) == 1999:
            spec = colspecs_99
            skiprows = 1
        elif int(year) in (2000, 2001, 2002, 2003, 2004):
            spec = colspecs_04
            skiprows = 1
        elif int(year) in (2005, 2006):
            spec = colspecs_23
            skiprows = 1
        else:
            spec = colspecs_23
            skiprows = 2

        res = requests.get(uri)
        lines = res.text.split('\n')
        line_length = len(lines[0])
        # print(lines[0])
        if lines[0][0] == '#':
            skiprows = 2
            if 'mm' in lines[0]:
                spec = colspecs_23

        str_buff = StringIO('\n'.join([process_line(l, line_length, i) for i, l in enumerate(lines)]))
        if log_uri:
            print(uri)
        
        df = pd.read_fwf(
            str_buff,
            names=spec.keys(),
            colspecs=[v[0] for v in spec.values()],
            skiprows=skiprows,
            dtype={k: v[1] for k, v in spec.items()},
            on_bad_lines='warn',
            # converters=converters
        )

        if 'minute' not in df.columns:
            df.loc[:, ('minute',)] = np.nan
            

        if 'tide' not in df.columns:
            df.loc[:, ('tide',)] = np.nan

        df = df[colspecs_23.keys()]
        df['source'] = uri
        hist_waves.append(df)
        
    out_df = pd.concat(hist_waves).apply(nan_cols)
    if save_frame:
        s3_location = f's3://gulf-waves/data/raw/historic_smd/station_id={station_id}/file.parquet'
        wr.s3.to_parquet(out_df, s3_location)
    else:
        return out_df, hist_waves

In [171]:
q.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 7043 entries, 0 to 7042
Data columns (total 16 columns):
 #   Column           Non-Null Count  Dtype  
---  ------           --------------  -----  
 0   year             7043 non-null   int64  
 1   month            7043 non-null   int64  
 2   day              7043 non-null   int64  
 3   hour             7043 non-null   int64  
 4   wind_dir         7043 non-null   int64  
 5   wind_spd         7043 non-null   float64
 6   gust             7043 non-null   float64
 7   wave_height      7043 non-null   float64
 8   dominant_period  7043 non-null   float64
 9   avg_period       7043 non-null   float64
 10  wave_direction   7043 non-null   int64  
 11  pressure         7043 non-null   float64
 12  air_temp         7043 non-null   float64
 13  water_temp       7043 non-null   float64
 14  dew_point        7043 non-null   float64
 15  visibility       7043 non-null   float64
dtypes: float64(10), int64(6)
memory usage: 880.5 KB


In [206]:
from tqdm.notebook import tqdm

errors = list()

for station_id, links in tqdm(bouy_data_links.items(), desc="Getting historic data"):
    try:
        # print(station_id)
        load_em_datums(station_id, links)
    except Exception as e:
        print(f'Error loading data for station: {station_id}')
        errors.append((station_id, links, e))

Getting historic data:   0%|          | 0/1315 [00:00<?, ?it/s]

Error loading data for station: 41009
Error loading data for station: 41029
Error loading data for station: 42360
Error loading data for station: 42370
Error loading data for station: 42887
Error loading data for station: 44008
Error loading data for station: 44027
Error loading data for station: 45165
Error loading data for station: 45176
Error loading data for station: 46027
Error loading data for station: 46029
Error loading data for station: 46094
Error loading data for station: ADKA2
Error loading data for station: BHRI3
Error loading data for station: BIGM4
Error loading data for station: CAPL1
Error loading data for station: CBBV2
Error loading data for station: CBLO1
Error loading data for station: CHAV3
Error loading data for station: CNDO1
Error loading data for station: FHPF1
Error loading data for station: FOXR1
Error loading data for station: FSKM2
Error loading data for station: GELO1
Error loading data for station: GISL1
Error loading data for station: GRMM4
Error loadin

In [211]:
len(errors)

50

In [215]:
errors[0]

('41009',
 [('1988',
   'https://www.ndbc.noaa.gov/view_text_file.php?filename=41009h1988.txt.gz&dir=data/historical/stdmet/'),
  ('1989',
   'https://www.ndbc.noaa.gov/view_text_file.php?filename=41009h1989.txt.gz&dir=data/historical/stdmet/'),
  ('1990',
   'https://www.ndbc.noaa.gov/view_text_file.php?filename=41009h1990.txt.gz&dir=data/historical/stdmet/'),
  ('1991',
   'https://www.ndbc.noaa.gov/view_text_file.php?filename=41009h1991.txt.gz&dir=data/historical/stdmet/'),
  ('1992',
   'https://www.ndbc.noaa.gov/view_text_file.php?filename=41009h1992.txt.gz&dir=data/historical/stdmet/'),
  ('1993',
   'https://www.ndbc.noaa.gov/view_text_file.php?filename=41009h1993.txt.gz&dir=data/historical/stdmet/'),
  ('1994',
   'https://www.ndbc.noaa.gov/view_text_file.php?filename=41009h1994.txt.gz&dir=data/historical/stdmet/'),
  ('1995',
   'https://www.ndbc.noaa.gov/view_text_file.php?filename=41009h1995.txt.gz&dir=data/historical/stdmet/'),
  ('1996',
   'https://www.ndbc.noaa.gov/view_

In [3]:
import json
with open('./errors.json') as f:
    errors_3 = json.load(f)

In [ ]:
errors_6 = list()

for station_id, links, error in tqdm(errors_5, desc="Reloading errored 2 historic data"):
    # load_em_datums(station_id, links, log_uri=True)
    try:
        # print(station_id)
        load_em_datums(station_id, links)
    except KeyboardInterrupt as e:
        raise e
    except Exception as e:
        
        print(f'Error loading data for station: {station_id}')
        errors_6.append((station_id, links, e))

Reloading errored 2 historic data:   0%|          | 0/3 [00:00<?, ?it/s]

In [40]:
len(errors_5)

3

In [254]:
print('hmm')

hmm


In [229]:
import json
with open('./errors.json', 'w') as f:
    json.dump([e[:2] for e in errors], f, indent=4)

In [39]:
z, frames = load_em_datums('SISW1', bouy_data_links['SISW1'], save_frame=False, log_uri=True)

# 99 starts 4 digit year
# 04 header off
# 05 start minute level
# 07 start #

https://www.ndbc.noaa.gov/view_text_file.php?filename=sisw1h1984.txt.gz&dir=data/historical/stdmet/
https://www.ndbc.noaa.gov/view_text_file.php?filename=sisw1h1985.txt.gz&dir=data/historical/stdmet/
https://www.ndbc.noaa.gov/view_text_file.php?filename=sisw1h1986.txt.gz&dir=data/historical/stdmet/
https://www.ndbc.noaa.gov/view_text_file.php?filename=sisw1h1987.txt.gz&dir=data/historical/stdmet/
https://www.ndbc.noaa.gov/view_text_file.php?filename=sisw1h1988.txt.gz&dir=data/historical/stdmet/
https://www.ndbc.noaa.gov/view_text_file.php?filename=sisw1h1989.txt.gz&dir=data/historical/stdmet/
https://www.ndbc.noaa.gov/view_text_file.php?filename=sisw1h1990.txt.gz&dir=data/historical/stdmet/
https://www.ndbc.noaa.gov/view_text_file.php?filename=sisw1h1991.txt.gz&dir=data/historical/stdmet/
https://www.ndbc.noaa.gov/view_text_file.php?filename=sisw1h1992.txt.gz&dir=data/historical/stdmet/
https://www.ndbc.noaa.gov/view_text_file.php?filename=sisw1h1993.txt.gz&dir=data/historical/stdmet/


In [41]:
z.info()

<class 'pandas.core.frame.DataFrame'>
Index: 318389 entries, 0 to 34738
Data columns (total 19 columns):
 #   Column           Non-Null Count   Dtype  
---  ------           --------------   -----  
 0   year             318389 non-null  int64  
 1   month            318389 non-null  int64  
 2   day              318389 non-null  int64  
 3   hour             318389 non-null  int64  
 4   minute           168178 non-null  float64
 5   wind_dir         309497 non-null  Int64  
 6   wind_spd         316865 non-null  float64
 7   gust             316633 non-null  float64
 8   wave_height      0 non-null       float64
 9   dominant_period  0 non-null       float64
 10  avg_period       0 non-null       float64
 11  wave_direction   0 non-null       Int64  
 12  pressure         310204 non-null  float64
 13  air_temp         310065 non-null  float64
 14  water_temp       0 non-null       float64
 15  dew_point        318389 non-null  float64
 16  visibility       0 non-null       float64
 1

In [225]:
z.sample(20)

year  month  day  hour  minute  wind_dir  wind_spd  gust  wave_height  \
723    2014      1   16     1    20.0       284       8.6  11.2          NaN   
6248     98      5   11     4     NaN       237       6.9   8.1         0.97   
20392  2017      9   12    14    10.0       216       6.2   8.7          NaN   
51466  2021     12   31    14    20.0       252       4.5   5.7          NaN   
4159     88     11    4    11     NaN       180      10.4  12.4         1.80   
13568  2018      4    5     7    20.0       344       7.3   8.9          NaN   
14808  2021      4   20    14    10.0      <NA>       8.8  10.7          NaN   
9043   2022      3    4    19    20.0        15       4.5   5.6          NaN   
16296  2011     12    6    14    20.0       101       6.5   7.8         2.31   
15120  2019      4   16    22    40.0        48       5.4   6.8         0.71   
13506    94     10   11     5     NaN       123       5.9   6.8          NaN   
2976   2010      3   19    18    20.0       310       5.4   6.5         1.10   
12345    92      9   15    16     NaN       174       0.8   1.7         1.50   
17033  2011     12   21    22    50.0       162       7.5   8.4         1.43   
13986    92     10   20     9     NaN        71       8.1  10.5         1.80   
7278   1999      6    1    15     NaN       105       6.0   7.3         1.87   
9483     90      7   20     0     NaN        72       4.7   5.7         1.20   
3110   1999      3    6    19     NaN       186       2.4   3.4         0.74   
9864   2015      7   27     8    50.0       204       7.5   8.9         1.02   
8986   2005      8    6    23     0.0       120       3.4   4.1         0.50   

       dominant_period  avg_period  wave_direction  pressure  air_temp  \
723                NaN         NaN            <NA>    1015.4      17.8   
6248              4.17        3.80            <NA>    1006.3      25.3   
20392              NaN         NaN            <NA>       NaN      26.8   
51466              NaN         NaN            <NA>    1019.5      21.0   
4159              6.20        5.00            <NA>    1012.6      23.3   
13568              NaN         NaN            <NA>    1016.2      22.6   
14808              NaN         NaN            <NA>    1013.1       NaN   
9043               NaN         NaN            <NA>    1023.2      23.4   
16296            10.81        6.66            <NA>    1021.1      23.7   
15120             6.67        4.66              14    1020.6      24.2   
13506              NaN         NaN            <NA>    1014.1      26.6   
2976             12.12        4.94            <NA>    1017.9      16.6   
12345             9.10        7.10            <NA>    1019.5      29.0   
17033            12.90        4.68            <NA>    1020.1      24.2   
13986             6.20        4.80            <NA>    1021.0      22.7   
7278              8.33        5.43            <NA>    1018.8      25.3   
9483              5.60        4.90            <NA>    1017.8      26.6   
3110              4.35        4.08            <NA>    1021.8      21.4   
9864              4.76        4.48             158    1012.5      25.7   
8986              7.14        5.67            <NA>    1015.5      28.9   

       water_temp  dew_point  visibility  tide  \
723          24.0        6.8         NaN   NaN   
6248         24.9      999.0         NaN   NaN   
20392        28.0       22.7         NaN   NaN   
51466        25.3       20.7         NaN   NaN   
4159         25.3      999.0         NaN   NaN   
13568        23.3       19.2         NaN   NaN   
14808        24.2      999.0         NaN   NaN   
9043         23.0       17.0         NaN   NaN   
16296        24.3       17.7         NaN   NaN   
15120         NaN       15.0         NaN   NaN   
13506        26.6      999.0         NaN   NaN   
2976         19.2       10.6         NaN   NaN   
12345        28.2      999.0         NaN   NaN   
17033        24.4       18.3         NaN   NaN   
13986        26.9    

In [66]:
def find_row_by_value(df, value):
    """
    Finds the first row in a DataFrame where the given value exists.

    Args:
        df: The Pandas DataFrame to search.
        value: The value to search for.

    Returns:
        The first row (as a Series) containing the value, or None if not found.
    """
    for index, row in df.iterrows():
        if value in row.values:
            return row
    return None

In [82]:
find_row_by_value(z, '16.7 99.0 99.00')

In [69]:
find_row_by_value(z, '16.7 99.0 99.00')

year                                                            2008
month                                                              1
day                                                                1
hour                                                               0
minute                                                             0
wind_dir                                                         NaN
wind_spd                                                         6.6
gust                                                             NaN
wave_height                                                      NaN
dominant_period                                                  NaN
avg_period                                                       NaN
wave_direction                                                   NaN
pressure                                                         NaN
air_temp                                                        19.6
water_temp                        

In [58]:
z[z.year == '#yr'].iloc[0].source

IndexError: single positional indexer is out-of-bounds

In [61]:
z[~pd.isna(z.tide)]

Empty DataFrame
Columns: [year, month, day, hour, minute, wind_dir, wind_spd, gust, wave_height, dominant_period, avg_period, wave_direction, pressure, air_temp, water_temp, dew_point, visibility, tide, source]
Index: []

In [40]:
z.iloc[0].source

'https://www.ndbc.noaa.gov/view_text_file.php?filename=41001h1976.txt.gz&dir=data/historical/stdmet/'

In [100]:
uri = 'https://www.ndbc.noaa.gov/view_text_file.php?filename=32st2h2008.txt.gz&dir=data/historical/stdmet/'
with urlopen(uri) as response:
            file = response.read().decode('utf-8')

In [99]:
line_counts = dict()
for l in file.split('\n'):
    

['YY MM DD hh WD   WSPD GST  WVHT  DPD   APD  MWD  BAR    ATMP  WTMP  DEWP  VIS',
 '76 06 01 18 226 07.9 99.0 99.00 99.00 99.00 999 1017.9  22.6  22.2 999.0 99.0',
 '76 06 01 21 230 07.8 99.0 99.00 99.00 99.00 999 1016.6  22.8  22.3 999.0 99.0',
 '76 06 02 00 211 08.0 99.0 99.00 99.00 99.00 999 1015.9  22.4  22.3 999.0 99.0',
 '76 06 02 03 219 09.3 99.0 99.00 99.00 99.00 999 1016.2  22.4  22.2 999.0 99.0',
 '76 06 02 06 224 09.1 99.0 99.00 99.00 99.00 999 1015.9  22.5  22.1 999.0 99.0',
 '76 06 02 09 210 09.0 99.0 99.00 99.00 99.00 999 1015.5  22.4  22.1 999.0 99.0',
 '76 06 02 12 210 09.6 99.0 99.00 99.00 99.00 999 1015.6  22.5  22.1 999.0 99.0',
 '76 06 02 15 224 09.6 99.0 99.00 99.00 99.00 999 1015.9  22.7  22.2 999.0 99.0',
 '76 06 02 18 222 08.2 99.0 99.00 99.00 99.00 999 1015.9  22.8  22.2 999.0 99.0',
 '76 06 02 21 211 09.9 99.0 99.00 99.00 99.00 999 1015.2  22.8  22.2 999.0 99.0',
 '76 06 03 00 216 08.2 99.0 99.00 99.00 99.00 999 1015.7  22.6  22.2 999.0 99.0',
 '76 06 03 03 22